<a href="https://colab.research.google.com/github/nrqrmz/jose-luis-nuno/blob/main/jose_luis_nuno.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [61]:
import pandas as pd
import numpy as np
import plotly.express as px

In [62]:
df_customers = pd.read_csv('olist_customers_dataset.csv')
# geolocation = pd.read_csv('olist_geolocation_dataset.csv')
df_items = pd.read_csv('olist_order_items_dataset.csv')
df_payments = pd.read_csv('olist_order_payments_dataset.csv')
df_reviews = pd.read_csv('olist_order_reviews_dataset.csv', encoding='latin1')
# order_reviews_clean = pd.read_csv('olist_order_reviews_dataset_clean.csv', encoding='latin1')
df_orders = pd.read_csv('olist_orders_dataset.csv')
df_products = pd.read_csv('olist_products_dataset.csv')
# df_sellers = pd.read_csv('olist_sellers_dataset.csv')
# category_translation = pd.read_csv('product_category_name_translation.csv')

In [63]:
pedidos_consolidados = df_payments.merge(df_orders, on='order_id').groupby(['order_id', 'customer_id'], as_index=False)['payment_value'].sum()
pedidos_consolidados.rename(columns={'payment_value': 'total_pago'}, inplace=True)

In [64]:
df_orders['order_purchase_timestamp'] = pd.to_datetime(df_orders['order_purchase_timestamp'], format='%d/%m/%Y %H:%M')

In [65]:
mi_fecha = pd.to_datetime('2018-10-18')

t1 = (
  df_orders
  .merge(df_customers, on='customer_id')
  .merge(pedidos_consolidados, on='order_id')
  .groupby('customer_unique_id', as_index=False)
  .agg(
      last_purchase=('order_purchase_timestamp', 'max'),
      frecuencia_score=('customer_id_x', 'nunique'),
      monetizacion_score=('total_pago', 'sum')
  )
)

t1['recencia_score'] = (mi_fecha - t1['last_purchase']).dt.days

In [66]:
total = t1[['customer_unique_id', 'recencia_score', 'frecuencia_score', 'monetizacion_score']]

In [67]:
rfm = total

In [68]:
rfm['R'] = pd.qcut(rfm['recencia_score'], q=5, labels=False)
rfm['R'] = 5 - rfm['R']

In [69]:
rfm['F'] = np.select(
    [
        rfm['frecuencia_score'] == 1,
        rfm['frecuencia_score'] == 2,
        rfm['frecuencia_score'] == 3,
        rfm['frecuencia_score'].isin([4, 5]),
        rfm['frecuencia_score'] >= 6
    ],
    [1, 2, 3, 4, 5],
    default=None
)

In [70]:
rfm['M'] = pd.qcut(rfm['monetizacion_score'], q=5, labels=False, duplicates='drop')
rfm['M'] = rfm['M'] + 1

In [71]:
rfm.head()

customer_unique_id  recencia_score  frecuencia_score  \
0  0000366f3b9a7992bf8c76cfdf3221e2             160                 1   
1  0000b849f77a49e4a4ce2b2a4ca5be3f             163                 1   
2  0000f46a3911fa3c0805444483337064             586                 1   
3  0000f6ccb0745a6a4b88665a16c9f078             370                 1   
4  0004aac84e0df4da2b147fca70cf8255             337                 1   

   monetizacion_score  R  F  M  
0              141.90  4  1  4  
1               27.19  4  1  1  
2               86.22  1  1  2  
3               43.62  2  1  1  
4              196.89  2  1  4

In [72]:
rfm['RFM_score'] = rfm['R'].astype(str) + rfm['F'].astype(str) + rfm['M'].astype(str)

In [73]:
# ids = [
#    '317cfc692e3f86c45c95697c61c853a6',
#    'bd06ce0e06ad77a7f681f1a4960a3cc6',
#    'b33336f46234b24a613ad9064d13106d',
#    '6f5b9d1cdccc4d28f0483a612edecacf',
#    '2878e5b88167faab17d4fb83a986d38b'
# ]

In [74]:
# rfm[rfm['customer_unique_id'].isin(ids)]

In [75]:
df = rfm

In [76]:
df.sort_values(by="monetizacion_score", ascending=False)

customer_unique_id  recencia_score  frecuencia_score  \
3826   0a0a92112bd4c708ca5fde585afaa872             383                 1   
26456  46450c74a0d8c5ca9395da1daac6c120              61                 3   
81961  da122df9eeddfedc1dc1f5349a1a690c             564                 2   
44447  763c8b1c9c68a0229c42c9fc6f662b93              94                 1   
82807  dc4802a71eae9be1dd28f5d788ceb526             612                 1   
...                                 ...             ...               ...   
67387  b33336f46234b24a613ad9064d13106d             118                 1   
71051  bd06ce0e06ad77a7f681f1a4960a3cc6             399                 1   
18643  317cfc692e3f86c45c95697c61c853a6              53                 1   
29977  4fa4365000c7090fcb8cad5713c6d3db              50                 1   
56518  968fac81e2c44fb6c1e3ac2a45e6a102              44                 1   

       monetizacion_score  R  F  M RFM_score  
3826             13664.08  2  1  5       215  
26456             9553.02  5  3  5       535  
81961             7571.63  1  2  5       125  
44447             7274.88  5  1  5       515  
82807             6929.31  1  1  5       115  
...                   ... .. .. ..       ...  
67387               10.89  5  1  1       511  
71051               10.07  2  1  1       211  
18643                9.59  5  1  1       511  
29977                0.00  5  1  1       511  
56518                0.00  5  1  1       511  

[96095 rows x 8 columns]

In [77]:
df_filtrado = df[df['F'].isin([1,5])]

In [78]:
df_filtrado['F'].value_counts()

F
1    93098
5       11
Name: count, dtype: int64

In [79]:
promedio_monetizacion = df_filtrado.groupby('F')['monetizacion_score'].mean().reset_index()

In [80]:
promedio_monetizacion

F  monetizacion_score
0  1          161.817111
1  5          828.941818

In [81]:
promedio_monetizacion['frecuencia_label'] = promedio_monetizacion['F'].map({1:'Baja', 5:'Alta'})

In [82]:
fig = px.bar(promedio_monetizacion,
             x='frecuencia_label',
             y='monetizacion_score',
             color='frecuencia_label',
             title='Valor monetario promedio: clientes menos frecuentes vs más frecuentes',
             labels={'frecuencia_label':'Segmento de frecuencia', 'monetizacion_score':'Valor monetario promedio ($)'}
            )
fig.show()

In [83]:
fig2 = px.box(df, x='frecuencia_score', y='monetizacion_score', color='F',
             title='Distribución de monetización por frecuencia')
fig2.show()

In [84]:
df['monetizacion_score'] = df['monetizacion_score'].astype(float)

fig = px.scatter(
    df,
    x='frecuencia_score',
    y='monetizacion_score',
    color='R',
    size='monetizacion_score',  # tamaño según monetización
    hover_data=['customer_unique_id'],
    title='Scatter plot: Frecuencia vs Monetización por Recencia'
)

fig.show()


In [85]:
df_payments_agg = (
    df_payments
    .groupby('order_id', as_index=False)
    .agg({
        'payment_value': 'sum',     # suma total del pago
        'payment_installments': 'max'  # número máximo de pagos
    })
)

In [87]:
df_merged = pd.merge(df_orders, df_customers, on='customer_id', how='inner')

# ===== 3️⃣ Merge con payments =====
df_merged = pd.merge(df_merged, df_payments_agg, on='order_id', how='inner')

In [88]:
df_merged = pd.merge(df_merged, df_reviews, on='order_id',how='inner')

In [89]:
df_merged[df_merged['order_status']=='canceled']

order_id                       customer_id  \
392    1b9ecfe83cdc259250e1a8aca174f0ad  6d6b50b66d79f80827b6d96751528d30   
608    714fb133a6730ab81fa1d3c1b2007291  e3fe72696c4713d64d3c10afe71e75ed   
609    714fb133a6730ab81fa1d3c1b2007291  e3fe72696c4713d64d3c10afe71e75ed   
1053   3a129877493c8189c59c60eb71d97c29  0913cdce793684e52bbfac69d87e91fd   
1125   00b1cb0320190ca0daa2c88b35206009  3532ba38a3fd242259a514ac2b6ae6b6   
...                                 ...                               ...   
98571  b159d0ce7cd881052da94fa165617b05  e0c3bc5ce0836b975d6b2a8ce7bb0e3e   
98690  e49e7ce1471b4693482d40c2bd3ad196  e4e7ab3f449aeb401f0216f86c2104db   
98925  6560fb10610771449cb0463c5ba12199  0d07d0a588caf93cc66b7a8aff86d2fe   
99065  3a3cddda5a7c27851bd96c3313412840  0b0d6095c5555fe083844281f6b093bb   
99129  a89abace0dcc01eeb267a9660b5ac126  2f0524a7b1b3845a1a57fcf3910c4333   

      order_status order_purchase_timestamp order_approved_at  \
392       canceled      2018-08-04 14:29:00  07/08/2018 04:10   
608       canceled      2018-01-26 21:34:00  26/01/2018 21:58   
609       canceled      2018-01-26 21:34:00  26/01/2018 21:58   
1053      canceled      2018-01-25 13:34:00  25/01/2018 13:50   
1125      canceled      2018-08-28 15:26:00               NaN   
...            ...                      ...               ...   
98571     canceled      2017-03-11 19:51:00  11/03/2017 19:51   
98690     canceled      2018-08-07 11:16:00               NaN   
98925     canceled      2017-10-01 22:26:00  01/10/2017 22:35   
99065     canceled      2018-08-31 16:13:00               NaN   
99129     canceled      2018-09-06 18:45:00               NaN   

      order_delivered_carrier_date order_delivered_customer_date  \
392                            NaN                           NaN   
608               29/01/2018 22:33                           NaN   
609               29/01/2018 22:33                           NaN   
1053              26/01/2018 21:42                           NaN   
1125                           NaN                           NaN   
...                            ...                           ...   
98571                          NaN                           NaN   
98690                          NaN                           NaN   
98925                          NaN                           NaN   
99065                          NaN                           NaN   
99129                          NaN                           NaN   

      order_estimated_delivery_date                customer_unique_id  \
392                14/08/2018 00:00  8ea097b1824dbd4d17af71b0afe04301   
608                22/02/2018 00:00  c4ebedb09beb89cc0314c5c0c33f8053   
609                22/02/2018 00:00  c4ebedb09beb89cc0314c5c0c33f8053   
1053               23/02/2018 00:00  11c3d6c93dea6ce86769a4835c171bd9   
1125               12/09/2018 00:00  4fa4365000c7090fcb8cad5713c6d3db   
...                             ...                               ...   
98571              30/03/2017 00:00  78a159045124eb7601951b917a42034f   
98690              10/08/2018 00:00  13d7bd0b05e18b00f415221b3bb69348   
98925              27/10/2017 00:00  0f75924cbbe60142068f4029d744b724   
99065              01/10/2018 00:00  e90598185d2427a35e32ef241a5c04aa   
99129              27/09/2018 00:00  d05c44a138277ad325d915c6b7ccbcdf   

       customer_zip_code_prefix          customer_city customer_state  \
392                        5514              sao paulo             SP   
608                        9961                diadema             SP   
609                        9961                diadema             SP   
1053                      87013                maringa             PR   
1125                       1151              sao paulo             SP   
...                         ...                    ...            ...   
98571                     89111                 gaspar             SC   
98690                      9810  sao bernardo d

In [90]:
df_merged[df_merged['order_id']=='10a045cdf6a5650c21e9cfeb60384c16']

order_id                       customer_id  \
60791  10a045cdf6a5650c21e9cfeb60384c16  a4b417188addbc05b26b72d5e44837a1   

      order_status order_purchase_timestamp order_approved_at  \
60791     canceled      2018-10-17 17:30:00               NaN   

      order_delivered_carrier_date order_delivered_customer_date  \
60791                          NaN                           NaN   

      order_estimated_delivery_date                customer_unique_id  \
60791              30/10/2018 00:00  87ab9fec999db8bd5774917de3cdf01c   

       customer_zip_code_prefix customer_city customer_state  payment_value  \
60791                     18077      sorocaba             SP          89.71   

       payment_installments                         review_id  review_score  \
60791                     1  716eff9ef436f351494c303085fcfcf5             1   

      review_comment_title                             review_comment_message  \
60791             "Troca "  "Por gentileza, trocar meu produto pois compre...   

      review_creation_date review_answer_timestamp  
60791     23/08/2018 00:00        24/08/2018 02:56

In [91]:
df_merged['satisfaction'] = np.where(df_merged['review_score'].isin([4,5]), 1, 0)

In [92]:
df_merged

order_id                       customer_id  \
0      e481f51cbdc54678b7cc49136f2d6af7  9ef432eb6251297304e76186b10a928d   
1      53cdb2fc8bc7dce0b6741e2150273451  b0830fb4747a6c6d20dea0b8c802d7ef   
2      47770eb9100c2d0c44946d9cf07ec65d  41ce2a54c0b03bf3443c3d931a367089   
3      949d5b44dbf5de918fe9c16f97b45f8a  f88197465ea7920adcdbec7375364d82   
4      ad21c59c0840e6cb83a9ceb5573f8159  8ab97904e6daea8866dbdbc4fb7aad2c   
...                                 ...                               ...   
99218  9c5dedf39a927c1b2549525ed64a053c  39bd1228ee8140590ac3aca26f2dfe00   
99219  63943bddc261676b46f01ca7ac2f7bd8  1fca14ff2861355f6e5f14306ff977a7   
99220  83c1379a015df1e13d02aae0204711ab  1aa71eb042121263aafbe80c1b562c9c   
99221  11c177c8e97725db2631073c19f07b62  b331b74b18dc79bcdf6532d51e1637c1   
99222  66dea50a8b16d9b4dee7af250b4be1a5  edb027a75a1449115f6b43211ae02a24   

      order_status order_purchase_timestamp order_approved_at  \
0        delivered      2017-10-02 10:56:00  02/10/2017 11:07   
1        delivered      2018-07-24 20:41:00  26/07/2018 03:24   
2        delivered      2018-08-08 08:38:00  08/08/2018 08:55   
3        delivered      2017-11-18 19:28:00  18/11/2017 19:45   
4        delivered      2018-02-13 21:18:00  13/02/2018 22:20   
...            ...                      ...               ...   
99218    delivered      2017-03-09 09:54:00  09/03/2017 09:54   
99219    delivered      2018-02-06 12:58:00  06/02/2018 13:10   
99220    delivered      2017-08-27 14:46:00  27/08/2017 15:04   
99221    delivered      2018-01-08 21:28:00  08/01/2018 21:36   
99222    delivered      2018-03-08 20:57:00  09/03/2018 11:20   

      order_delivered_carrier_date order_delivered_customer_date  \
0                 04/10/2017 19:55              10/10/2017 21:25   
1                 26/07/2018 14:31              07/08/2018 15:27   
2                 08/08/2018 13:50              17/08/2018 18:06   
3                 22/11/2017 13:39              02/12/2017 00:28   
4                 14/02/2018 19:46              16/02/2018 18:17   
...                            ...                           ...   
99218             10/03/2017 11:18              17/03/2017 15:08   
99219             07/02/2018 23:22              28/02/2018 17:37   
99220             28/08/2017 20:52              21/09/2017 11:24   
99221             12/01/2018 15:35              25/01/2018 23:32   
99222             09/03/2018 22:11              16/03/2018 13:08   

      order_estimated_delivery_date                customer_unique_id  \
0                  18/10/2017 00:00  7c396fd4830fd04220f754e42b4e5bff   
1                  13/08/2018 00:00  af07308b275d755c9edb36a90c618231   
2                  04/09/2018 00:00  3a653a41f6f9fc3d2a113cf8398680e8   
3                  15/12/2017 00:00  7c142cf63193a1473d2e66489a9ae977   
4                  26/02/2018 00:00  72632f0f9dd73dfee390c9b22eb56dd6   
...                             ...                               ...   
99218              28/03/2017 00:00  6359f309b166b0196dbf7ad2ac62bb5a   
99219              02/03/2018 00:00  da62f9e57a76d978d02ab5362c509660   
99220              27/09/2017 00:00  737520a9aad80b3fbbdad19b66b37b30   
99221              15/02/2018 00:00  5097a5312c8b157bb7be58ae360ef43c   
99222              03/04/2018 00:00  60350aa974b26ff12caad89e55993bd6   

       customer_zip_code_prefix  ... customer_state payment_value  \
0                          3149  ...             SP         38.71   
1                         47813  ...             BA        141.46   
2                         75265  ...             GO        179.12   
3                         59296  ...             RN         72.20   
4                          9195  ...             SP         28.62   
...                         ...  ...            ...           ...   
99218                     12209  ...             SP         85.08   
99219                     11722  ...             SP        195.00   
99220     

In [94]:
df_merged = df_merged.drop_duplicates(subset=['order_id', 'customer_id'])

In [95]:
df_merged

order_id                       customer_id  \
0      e481f51cbdc54678b7cc49136f2d6af7  9ef432eb6251297304e76186b10a928d   
1      53cdb2fc8bc7dce0b6741e2150273451  b0830fb4747a6c6d20dea0b8c802d7ef   
2      47770eb9100c2d0c44946d9cf07ec65d  41ce2a54c0b03bf3443c3d931a367089   
3      949d5b44dbf5de918fe9c16f97b45f8a  f88197465ea7920adcdbec7375364d82   
4      ad21c59c0840e6cb83a9ceb5573f8159  8ab97904e6daea8866dbdbc4fb7aad2c   
...                                 ...                               ...   
99218  9c5dedf39a927c1b2549525ed64a053c  39bd1228ee8140590ac3aca26f2dfe00   
99219  63943bddc261676b46f01ca7ac2f7bd8  1fca14ff2861355f6e5f14306ff977a7   
99220  83c1379a015df1e13d02aae0204711ab  1aa71eb042121263aafbe80c1b562c9c   
99221  11c177c8e97725db2631073c19f07b62  b331b74b18dc79bcdf6532d51e1637c1   
99222  66dea50a8b16d9b4dee7af250b4be1a5  edb027a75a1449115f6b43211ae02a24   

      order_status order_purchase_timestamp order_approved_at  \
0        delivered      2017-10-02 10:56:00  02/10/2017 11:07   
1        delivered      2018-07-24 20:41:00  26/07/2018 03:24   
2        delivered      2018-08-08 08:38:00  08/08/2018 08:55   
3        delivered      2017-11-18 19:28:00  18/11/2017 19:45   
4        delivered      2018-02-13 21:18:00  13/02/2018 22:20   
...            ...                      ...               ...   
99218    delivered      2017-03-09 09:54:00  09/03/2017 09:54   
99219    delivered      2018-02-06 12:58:00  06/02/2018 13:10   
99220    delivered      2017-08-27 14:46:00  27/08/2017 15:04   
99221    delivered      2018-01-08 21:28:00  08/01/2018 21:36   
99222    delivered      2018-03-08 20:57:00  09/03/2018 11:20   

      order_delivered_carrier_date order_delivered_customer_date  \
0                 04/10/2017 19:55              10/10/2017 21:25   
1                 26/07/2018 14:31              07/08/2018 15:27   
2                 08/08/2018 13:50              17/08/2018 18:06   
3                 22/11/2017 13:39              02/12/2017 00:28   
4                 14/02/2018 19:46              16/02/2018 18:17   
...                            ...                           ...   
99218             10/03/2017 11:18              17/03/2017 15:08   
99219             07/02/2018 23:22              28/02/2018 17:37   
99220             28/08/2017 20:52              21/09/2017 11:24   
99221             12/01/2018 15:35              25/01/2018 23:32   
99222             09/03/2018 22:11              16/03/2018 13:08   

      order_estimated_delivery_date                customer_unique_id  \
0                  18/10/2017 00:00  7c396fd4830fd04220f754e42b4e5bff   
1                  13/08/2018 00:00  af07308b275d755c9edb36a90c618231   
2                  04/09/2018 00:00  3a653a41f6f9fc3d2a113cf8398680e8   
3                  15/12/2017 00:00  7c142cf63193a1473d2e66489a9ae977   
4                  26/02/2018 00:00  72632f0f9dd73dfee390c9b22eb56dd6   
...                             ...                               ...   
99218              28/03/2017 00:00  6359f309b166b0196dbf7ad2ac62bb5a   
99219              02/03/2018 00:00  da62f9e57a76d978d02ab5362c509660   
99220              27/09/2017 00:00  737520a9aad80b3fbbdad19b66b37b30   
99221              15/02/2018 00:00  5097a5312c8b157bb7be58ae360ef43c   
99222              03/04/2018 00:00  60350aa974b26ff12caad89e55993bd6   

       customer_zip_code_prefix  ... customer_state payment_value  \
0                          3149  ...             SP         38.71   
1                         47813  ...             BA        141.46   
2                         75265  ...             GO        179.12   
3                         59296  ...             RN         72.20   
4                          9195  ...             SP         28.62   
...                         ...  ...            ...           ...   
99218                     12209  ...             SP         85.08   
99219                     11722  ...             SP        195.00   
99220     

In [96]:
# Merge de items con products
df_items_products = pd.merge(df_items, df_products, on='product_id', how='left')

# Agregamos a nivel de pedido
df_items_agg = df_items_products.groupby(['order_id',"product_category_name"]).agg({
    'order_item_id': 'count',           # número de items por pedido
    'price': 'sum',                     # valor total de los items
    'product_weight_g': 'sum',          # peso total del pedido
    'product_length_cm': 'sum',         # largo total
    'product_height_cm': 'sum',         # altura total
    'product_width_cm': 'sum'           # ancho total
}).reset_index()

In [97]:
df_items_agg

order_id   product_category_name  \
0      00010242fe8c5a6d1ba2dd792cb16214              cool_stuff   
1      00018f77f2f0320c557190d7a144bdd3                pet_shop   
2      000229ec398224ef6ca0657da4fc703e        moveis_decoracao   
3      00024acbcdf0a6daa1e931b038114c75              perfumaria   
4      00042b26cf59d7ce69dfabb4e55b4fd9      ferramentas_jardim   
...                                 ...                     ...   
98014  fffc94f6ce00a00581880bf54a75a037   utilidades_domesticas   
98015  fffcd46ef2263f404302a634eb57f7eb  informatica_acessorios   
98016  fffce4705a9662cd70adb13d4a31832d           esporte_lazer   
98017  fffe18544ffabc95dfada21779c9644f  informatica_acessorios   
98018  fffe41c64501cc87c801fd61db3f6244         cama_mesa_banho   

       order_item_id   price  product_weight_g  product_length_cm  \
0                  1   58.90             650.0               28.0   
1                  1  239.90           30000.0               50.0   
2                  1  199.00            3050.0               33.0   
3                  1   12.99             200.0               16.0   
4                  1  199.90            3750.0               35.0   
...              ...     ...               ...                ...   
98014              1  299.99           10150.0               89.0   
98015              1  350.00            8950.0               45.0   
98016              1   99.90             967.0               21.0   
98017              1   55.99             100.0               20.0   
98018              1   43.00             600.0               30.0   

       product_height_cm  product_width_cm  
0                    9.0              14.0  
1                   30.0              40.0  
2                   13.0              33.0  
3                   10.0              15.0  
4                   40.0              30.0  
...                  ...               ...  
98014               15.0              40.0  
98015               26.0              38.0  
98016               24.0              19.0  
98017               20.0              20.0  
98018                3.0              19.0  

[98019 rows x 8 columns]

In [100]:
df_merged = pd.merge(df_merged,df_items_agg, on='order_id', how='inner')

In [101]:
df_merged

order_id                       customer_id  \
0      e481f51cbdc54678b7cc49136f2d6af7  9ef432eb6251297304e76186b10a928d   
1      53cdb2fc8bc7dce0b6741e2150273451  b0830fb4747a6c6d20dea0b8c802d7ef   
2      47770eb9100c2d0c44946d9cf07ec65d  41ce2a54c0b03bf3443c3d931a367089   
3      949d5b44dbf5de918fe9c16f97b45f8a  f88197465ea7920adcdbec7375364d82   
4      ad21c59c0840e6cb83a9ceb5573f8159  8ab97904e6daea8866dbdbc4fb7aad2c   
...                                 ...                               ...   
97270  9c5dedf39a927c1b2549525ed64a053c  39bd1228ee8140590ac3aca26f2dfe00   
97271  63943bddc261676b46f01ca7ac2f7bd8  1fca14ff2861355f6e5f14306ff977a7   
97272  83c1379a015df1e13d02aae0204711ab  1aa71eb042121263aafbe80c1b562c9c   
97273  11c177c8e97725db2631073c19f07b62  b331b74b18dc79bcdf6532d51e1637c1   
97274  66dea50a8b16d9b4dee7af250b4be1a5  edb027a75a1449115f6b43211ae02a24   

      order_status order_purchase_timestamp order_approved_at  \
0        delivered      2017-10-02 10:56:00  02/10/2017 11:07   
1        delivered      2018-07-24 20:41:00  26/07/2018 03:24   
2        delivered      2018-08-08 08:38:00  08/08/2018 08:55   
3        delivered      2017-11-18 19:28:00  18/11/2017 19:45   
4        delivered      2018-02-13 21:18:00  13/02/2018 22:20   
...            ...                      ...               ...   
97270    delivered      2017-03-09 09:54:00  09/03/2017 09:54   
97271    delivered      2018-02-06 12:58:00  06/02/2018 13:10   
97272    delivered      2017-08-27 14:46:00  27/08/2017 15:04   
97273    delivered      2018-01-08 21:28:00  08/01/2018 21:36   
97274    delivered      2018-03-08 20:57:00  09/03/2018 11:20   

      order_delivered_carrier_date order_delivered_customer_date  \
0                 04/10/2017 19:55              10/10/2017 21:25   
1                 26/07/2018 14:31              07/08/2018 15:27   
2                 08/08/2018 13:50              17/08/2018 18:06   
3                 22/11/2017 13:39              02/12/2017 00:28   
4                 14/02/2018 19:46              16/02/2018 18:17   
...                            ...                           ...   
97270             10/03/2017 11:18              17/03/2017 15:08   
97271             07/02/2018 23:22              28/02/2018 17:37   
97272             28/08/2017 20:52              21/09/2017 11:24   
97273             12/01/2018 15:35              25/01/2018 23:32   
97274             09/03/2018 22:11              16/03/2018 13:08   

      order_estimated_delivery_date                customer_unique_id  \
0                  18/10/2017 00:00  7c396fd4830fd04220f754e42b4e5bff   
1                  13/08/2018 00:00  af07308b275d755c9edb36a90c618231   
2                  04/09/2018 00:00  3a653a41f6f9fc3d2a113cf8398680e8   
3                  15/12/2017 00:00  7c142cf63193a1473d2e66489a9ae977   
4                  26/02/2018 00:00  72632f0f9dd73dfee390c9b22eb56dd6   
...                             ...                               ...   
97270              28/03/2017 00:00  6359f309b166b0196dbf7ad2ac62bb5a   
97271              02/03/2018 00:00  da62f9e57a76d978d02ab5362c509660   
97272              27/09/2017 00:00  737520a9aad80b3fbbdad19b66b37b30   
97273              15/02/2018 00:00  5097a5312c8b157bb7be58ae360ef43c   
97274              03/04/2018 00:00  60350aa974b26ff12caad89e55993bd6   

       customer_zip_code_prefix  ... review_creation_date  \
0                          3149  ...     11/10/2017 00:00   
1                         47813  ...     08/08/2018 00:00   
2                         75265  ...     18/08/2018 00:00   
3                         59296  ...     03/12/2017 00:00   
4                          9195  ...     17/02/2018 00:00   
...                         ...  ...                  ...   
97270                     12209  ...     22/03/2017 00:00   
97271                     11722  ...     01/03/2018 00:00   
97272                     45920  ...     22/09/2017 00:00   
97273                

In [104]:
df_merged.columns

Index(['order_id', 'customer_id', 'order_status', 'order_purchase_timestamp',
       'order_approved_at', 'order_delivered_carrier_date',
       'order_delivered_customer_date', 'order_estimated_delivery_date',
       'customer_unique_id', 'customer_zip_code_prefix', 'customer_city',
       'customer_state', 'payment_value', 'payment_installments', 'review_id',
       'review_score', 'review_comment_title', 'review_comment_message',
       'review_creation_date', 'review_answer_timestamp', 'satisfaction',
       'product_category_name', 'order_item_id', 'price', 'product_weight_g',
       'product_length_cm', 'product_height_cm', 'product_width_cm'],
      dtype='object')

In [111]:
df_model = df_merged[~df_merged['order_status'].isin(['canceled', 'unavailable'])]
df_model.drop(columns=[
    "order_item_id",
    "price",
    "product_weight_g",
    "product_length_cm",
    "product_height_cm",
    "order_item_id",
    "customer_id",
    "customer_unique_id",
    "order_id",
    "review_score",
    "review_comment_title",
    "review_comment_message",
    "review_creation_date",
    "review_answer_timestamp",
    "order_estimated_delivery_date",
    "order_delivered_carrier_date",
    "customer_zip_code_prefix",
    "order_approved_at",
    "review_id",
    "product_width_cm"
    ], inplace=True)

/tmp/ipython-input-169733852.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [118]:
df_model = df_model.dropna(subset=['order_delivered_customer_date'])
df_model['order_delivered_customer_date'] = pd.to_datetime(df_model['order_delivered_customer_date'], format='%d/%m/%Y %H:%M')

In [119]:
df_model['dias_entrega'] = (df_model['order_delivered_customer_date'] - df_model['order_purchase_timestamp']).dt.days

In [120]:
df_model

order_status order_purchase_timestamp order_delivered_customer_date  \
0        delivered      2017-10-02 10:56:00           2017-10-10 21:25:00   
1        delivered      2018-07-24 20:41:00           2018-08-07 15:27:00   
2        delivered      2018-08-08 08:38:00           2018-08-17 18:06:00   
3        delivered      2017-11-18 19:28:00           2017-12-02 00:28:00   
4        delivered      2018-02-13 21:18:00           2018-02-16 18:17:00   
...            ...                      ...                           ...   
97270    delivered      2017-03-09 09:54:00           2017-03-17 15:08:00   
97271    delivered      2018-02-06 12:58:00           2018-02-28 17:37:00   
97272    delivered      2017-08-27 14:46:00           2017-09-21 11:24:00   
97273    delivered      2018-01-08 21:28:00           2018-01-25 23:32:00   
97274    delivered      2018-03-08 20:57:00           2018-03-16 13:08:00   

                 customer_city customer_state  payment_value  \
0                    sao paulo             SP          38.71   
1                    barreiras             BA         141.46   
2                   vianopolis             GO         179.12   
3      sao goncalo do amarante             RN          72.20   
4                  santo andre             SP          28.62   
...                        ...            ...            ...   
97270      sao jose dos campos             SP          85.08   
97271             praia grande             SP         195.00   
97272              nova vicosa             BA         271.01   
97273                  japuiba             RJ         441.16   
97274                     lapa             PR          86.86   

       payment_installments  satisfaction   product_category_name  \
0                         1             1   utilidades_domesticas   
1                         1             1              perfumaria   
2                         3             1              automotivo   
3                         1             1                pet_shop   
4                         1             1               papelaria   
...                     ...           ...                     ...   
97270                     3             1            beleza_saude   
97271                     3             1                   bebes   
97272                     5             1      eletrodomesticos_2   
97273                     4             0  informatica_acessorios   
97274                     1             1            beleza_saude   

       dias_entrega  
0                 8  
1                13  
2                 9  
3                13  
4                 2  
...             ...  
97270             8  
97271            22  
97272            24  
97273            17  
97274             7  

[95233 rows x 10 columns]

In [121]:
df_model_final = df_model.drop(columns=['order_delivered_customer_date','order_purchase_timestamp','customer_city'])

In [122]:
df_model_final

order_status customer_state  payment_value  payment_installments  \
0        delivered             SP          38.71                     1   
1        delivered             BA         141.46                     1   
2        delivered             GO         179.12                     3   
3        delivered             RN          72.20                     1   
4        delivered             SP          28.62                     1   
...            ...            ...            ...                   ...   
97270    delivered             SP          85.08                     3   
97271    delivered             SP         195.00                     3   
97272    delivered             BA         271.01                     5   
97273    delivered             RJ         441.16                     4   
97274    delivered             PR          86.86                     1   

       satisfaction   product_category_name  dias_entrega  
0                 1   utilidades_domesticas             8  
1                 1              perfumaria            13  
2                 1              automotivo             9  
3                 1                pet_shop            13  
4                 1               papelaria             2  
...             ...                     ...           ...  
97270             1            beleza_saude             8  
97271             1                   bebes            22  
97272             1      eletrodomesticos_2            24  
97273             0  informatica_acessorios            17  
97274             1            beleza_saude             7  

[95233 rows x 7 columns]

In [123]:
from sklearn.model_selection import train_test_split


X = df_model_final.drop(columns='satisfaction')
y= df_model_final['satisfaction']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=.2, random_state=42)

In [124]:
from sklearn.preprocessing import OneHotEncoder

#Create X_train_cat and X_test_cat
X_train_cat = X_train.select_dtypes(include=['object'])
X_test_cat = X_test.select_dtypes(include=['object'])

# Define our OneHotEncoder and fit it on the train set
ohe = OneHotEncoder(drop='if_binary', sparse_output=False)
ohe.fit(X_train_cat.select_dtypes(include=['object']))

# Transform both train and test set
X_train_cat = pd.DataFrame(ohe.transform(X_train_cat), columns=ohe.get_feature_names_out())
X_test_cat = pd.DataFrame(ohe.transform(X_test_cat), columns=ohe.get_feature_names_out())

In [125]:
from sklearn.preprocessing import StandardScaler

# extract only numerical data
X_train_num = X_train.select_dtypes(["int", "float"])
X_test_num = X_test.select_dtypes(["int", "float"])

# Define our Scaler and fit_transform on the train set and transform the test set
sc = StandardScaler()
X_train_num = sc.fit_transform(X_train_num)
X_test_num = sc.transform(X_test_num)

# Create two dataframe with the columns name
X_train_num = pd.DataFrame(X_train_num, columns=sc.get_feature_names_out())
X_test_num = pd.DataFrame(X_test_num, columns=sc.get_feature_names_out())

In [126]:
X_train_preprocessed = pd.concat((X_train_num, X_train_cat), axis=1)
X_test_preprocessed = pd.concat((X_test_num, X_test_cat), axis=1)

In [127]:
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report, f1_score, precision_score, recall_score, roc_auc_score
model = LogisticRegression(class_weight='balanced')

model.fit(X_train_preprocessed, y_train)

# compute accuracy
model.score(X_test_preprocessed, y_test)

0.6790045676484485

In [129]:
from sklearn.ensemble import RandomForestClassifier
forest_model = RandomForestClassifier()
forest_model.fit(X_train_preprocessed, y_train)
print("Accuracy del modelo:", forest_model.score(X_test_preprocessed, y_test))

Accuracy del modelo: 0.7746626765369875


In [130]:
forest_model.fit(X_train_preprocessed, y_train)
forest_model.score(X_test_preprocessed, y_test)

0.7743476662991547

In [131]:
df_model_final['satisfaction'].value_counts()

satisfaction
1    74957
0    20276
Name: count, dtype: int64